# Moving Reflection Separation Prototype  
Authors:  
Ben Koren  
Tal Balelty

In [266]:
import gc
import cv2
import numpy as np
import matplotlib.pyplot as plt
from moviepy.editor import *
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [267]:
class Configuration:
  def __init__(self):
    self.window_size = 10
    self.min_val = 2.5
    # TAL
    self.path_to_video = "/content/drive/MyDrive/project images/הזזת השתקפות אצל בן.mp4"
    self.path_to_transmission_video = "/content/drive/MyDrive/project images/transmission video.avi"
    self.path_to_reflection_video = "/content/drive/MyDrive/project images/reflection video.avi"
    # BEN
    # self.path_to_video = "/content/drive/MyDrive/WhatsApp Video 2021-10-11 at 16.25.08.mp4"
    # self.path_to_transmission_video = "/content/drive/MyDrive/transmission video.avi"
    # self.path_to_reflection_video = "/content/drive/MyDrive/reflection video.avi"

# Separation Functions

In [268]:
def process_video_separation(video, extraction_function, path):
  cfg = Configuration()
  separated_video = dict()
  window = list()
  ret = True
  separated_frame_index = 0
  fps = round(video.get(cv2.CAP_PROP_FPS))
  skip_frames = fps // cfg.window_size
  for i in range(fps):
    ret, frame = video.read()
    if ret:
      if i % skip_frames == 0:
        window.append(frame)

    else:
      return null
  
  extraction_function(separated_frame_index, separated_video, window)
  separated_frame_index += 1
  
  # plt.figure(figsize=(5,8))
  # plt.imshow(np.rot90(separated_video[0], k=-1, axes=(0,1)))
  # plt.show()

  i = fps
  while (ret):
    ret, frame = video.read()
    if i % skip_frames == 0:
      window = window[1:]
      if frame is not None:
        window.append(frame)
        extraction_function(separated_frame_index, separated_video, window)
        separated_frame_index += 1
    
    i += 1

  separated_video = list(dict(sorted(separated_video.items())).values())
  separated_video = np.rot90(separated_video, k=-1, axes=(1,2))
  save_video(separated_video, path)
  return separated_video

In [269]:
def extract_transmission_layer(frame_number, separated_video, window):
  separated_image = np.median(window, axis=0).astype(np.uint8)
  separated_video[frame_number] = separated_image

In [270]:
def extract_reflection_layer(frame_number, separated_video, window):
  cfg = Configuration()
  grey_window = list()

  for i, frame in enumerate(window):
    grey_window.append(cv2.cvtColor(frame, cv2.COLOR_RGB2GRAY))

  mean = np.mean(grey_window, axis=0)
  threshold = cfg.min_val * np.std(grey_window, axis=0)
  mask = (grey_window[0] < mean - threshold) | (mean + threshold < grey_window[0])
  mask = mask[:, :, np.newaxis]
  mask = np.repeat(mask, 3, axis=2)

  # mean = np.mean(window, axis=0) # try median
  # threshold = min_val * np.std(window, axis=0)
  # mask = (window[0] < mean - threshold) | (mean + threshold < window[0])
  # for i, row in enumerate(mask):
  #   for j, pixel in enumerate(row):
  #     if False in pixel:
  #       mask[i,j] = [False, False, False]

  separated_video[frame_number] = np.where(mask, window[0], 0)

In [271]:
# def median_RGB(pixels):
#   r_median = statistics.median(pixels[:,0])
#   g_median = statistics.median(pixels[:,1])
#   b_median = statistics.median(pixels[:,2])

#   return (r_median, g_median, b_median)

In [272]:
def save_video(video, path):
  cfg = Configuration()
  h, w, _ = video[0].shape
  fourcc = cv2.VideoWriter_fourcc(*'XVID')
  out = cv2.VideoWriter(path, fourcc, cfg.window_size, (w, h))

  for i in range(len(video)):
    out.write(video[i])

  out.release()
  cv2.destroyAllWindows()
  print(path + "\nVideo made successfully")

## Transmission Extraction

In [273]:
gc.collect()
cfg = Configuration()
video = cv2.VideoCapture(cfg.path_to_video)
%time transmission_video = process_video_separation(video, extract_transmission_layer, cfg.path_to_transmission_video)
clip = VideoFileClip(cfg.path_to_transmission_video)
clip.ipython_display(width=300)

/content/drive/MyDrive/project images/transmission video.avi
Video made successfully
CPU times: user 14.5 s, sys: 97.6 ms, total: 14.6 s
Wall time: 14.1 s


 99%|█████████▊| 78/79 [00:00<00:00, 150.73it/s]


## Reflection Extraction

In [274]:
gc.collect()
video = cv2.VideoCapture(cfg.path_to_video)
%time reflection_video = process_video_separation(video, extract_reflection_layer, cfg.path_to_reflection_video)
clip = VideoFileClip(cfg.path_to_reflection_video)
clip.ipython_display(width=300)

/content/drive/MyDrive/project images/reflection video.avi
Video made successfully
CPU times: user 5.55 s, sys: 144 ms, total: 5.69 s
Wall time: 5.15 s


 99%|█████████▊| 78/79 [00:00<00:00, 127.23it/s]
